<center>  <h1> Bitcoin prices and the shape of the globe </h1></center>

[Why Bitcoin price is increasing amid Russia-Ukraine war](https://www.financialexpress.com/digital-currency/why-bitcoin-price-is-increasing-amid-russia-ukraine-war/2447933/)

# **¿Which could be the bitcoin price next week?**


## Read bitcoin data

In [21]:
using CSV, DataFrames, Dates, PlotlyJS

dataBitcoin = CSV.read("Datasets/Bitcoin.csv",DataFrame);
dataBitcoin.Price .= replace.(dataBitcoin.Price, "," => "");
dataBitcoin.PriceFloat = parse.(Float64, dataBitcoin.Price);
dataBitcoin.Date = Dates.Date.(dataBitcoin.Date, "u d, yyyy")
dataBitcoin[1:10,:]

10×8 DataFrame
 Row │ Date        Price     Open      High      Low       Vol.     Change %   ⋯
     │ Date        String15  String15  String15  String15  String7  String7    ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ 2022-03-07  38014.8   38,420.6  38,543.2  37,597.7  2.14B    -1.01%     ⋯
   2 │ 2022-03-06  38403.1   39,396.3  39,668.1  38,115.0  1.93B    -2.52%
   3 │ 2022-03-05  39395.8   39,142.8  39,600.2  38,626.1  1.50B    0.65%
   4 │ 2022-03-04  39142.7   42,463.0  42,848.7  38,594.9  3.21B    -7.82%
   5 │ 2022-03-03  42463.0   43,912.8  44,077.2  41,840.8  74.11K   -3.30%     ⋯
   6 │ 2022-03-02  43912.8   44,420.3  45,294.2  43,361.3  80.82K   -1.14%
   7 │ 2022-03-01  44420.3   43,187.2  44,900.5  42,876.6  90.67K   2.85%
   8 │ 2022-02-28  43188.2   37,707.2  43,977.8  37,458.9  108.07K  14.59%
   9 │ 2022-02-27  37689.1   39,116.6  39,838.5  37,062.3  66.14K   -3.65%     ⋯
  10 │ 2022-02-26  39115.5   39,221.6  40,094.5  38,639.1  41.55K   -0.24%
                                                                1 column omitted

In [22]:
plot(scatter(x=dataBitcoin.Date, y= dataBitcoin.PriceFloat/1000, mode="markers+lines", name="Price",  legend=:topright),
             Layout(title="Bitcoin Price at 2022",  xaxis_title="Time (day - month)",  yaxis_title="Price (k\$)"))

data: [
  "scatter with fields legend, mode, name, type, x, and y"
]

layout: "layout with fields margin, title, xaxis, and yaxis"

Least squares formulation:

$$\tilde{x} = \mbox{arg min}_{x} \| Ax - b \|_2^2$$

In [23]:
N = size(dataBitcoin.PriceFloat,1);
A = Array((1:N));
b = Array(dataBitcoin.PriceFloat);
A = [ones(N,1) A];
println("Matrix A: \n",size(A),A)
println(" ")
println("Matrix b: \n",size(b),b)

Matrix A: 
(29, 2)[1.0 1.0; 1.0 2.0; 1.0 3.0; 1.0 4.0; 1.0 5.0; 1.0 6.0; 1.0 7.0; 1.0 8.0; 1.0 9.0; 1.0 10.0; 1.0 11.0; 1.0 12.0; 1.0 13.0; 1.0 14.0; 1.0 15.0; 1.0 16.0; 1.0 17.0; 1.0 18.0; 1.0 19.0; 1.0 20.0; 1.0 21.0; 1.0 22.0; 1.0 23.0; 1.0 24.0; 1.0 25.0; 1.0 26.0; 1.0 27.0; 1.0 28.0; 1.0 29.0]
 
Matrix b: 
(29,)[38014.8, 38403.1, 39395.8, 39142.7, 42463.0, 43912.8, 44420.3, 43188.2, 37689.1, 39115.5, 39209.6, 38339.2, 37224.6, 38248.2, 37017.7, 38355.0, 40090.3, 40000.1, 40552.8, 43883.6, 44544.4, 42550.3, 42061.1, 42205.2, 42388.4, 43521.0, 44388.9, 44038.2, 43833.9]


## Plot the **objective function**:

$$ f(x,y) = \sum_1^{N} (A\cdot X-b)\cdot(A\cdot X - b)^t $$

with $X = (x,y)^t$.

In [24]:
function f(x,y) 
    sum((A[:,1]*x+A[:,2]*y-b)*transpose((A[:,1]*x+A[:,2]*y-b)))
end

M = 100
x = LinRange(-5e4, 5e4, M)
y = LinRange(-5e4, 5e4, M)

F = Array{Float64}(undef,M,M)

for i in 1:1:M, j in 1:1:M
    F[i,j] = f(x[i],y[j])
end

PlotlyJS.plot([PlotlyJS.surface(x=x,y=y,z=F)])

data: [
  "surface with fields type, x, y, and z"
]

layout: "layout with field margin"

Least squares solution:

$$\tilde{x} = \mbox{arg min}_{x} J(\mathbf x) = \mbox{arg min}_{x} \| Ax - b \|_2^2 \\
J(x) = \| Ax - b\|_2^2 = ( Ax - b )^T ( Ax - b ) = (A x)^T (A x) - (A x)^T b - b^T (A x) + b^T b\\
J(x) = x^T A^T Ax - 2 x^T A^T b + b^T b $$

Now **minimizing** $J(x)$ w.r.t $x$:

$$ \frac{\partial J(x)}{\partial  x} = - 2 A^T b + 2 A^T A x = 0 $$

We obtain the [normal equations](https://en.wikipedia.org/wiki/Linear_least_squares#Derivation_of_the_normal_equations):

$$A^T A x = A^T b$$

The solution:

$$x = (A^T A)^{-1} A^T  b = A^+ b$$

With $A^+ = (A^T A)^{-1} A^T$ the Moore-Penrose pseudoinverse of $A$.

# Arrange data to compute least squares

Structure data to compute least squares:

## Least solution Squares in Julia

https://www.matecdev.com/posts/julia-least-squares-qr.html

* Using the unique least squares approximate solution of overdetermined equations:

$$(A^T A)^{-1} A^T$$

In [25]:
transpose(A)*A

2×2 Matrix{Float64}:
  29.0   435.0
 435.0  8555.0

In [26]:
beta1 = inv(transpose(A)*A)*(transpose(A)*b)

2-element Vector{Float64}:
 38722.227832512275
   150.00733990147995

* Using the Moore-Penrose pseudoinverse:

In [27]:
using LinearAlgebra

xhat2 = pinv(A)*b

2-element Vector{Float64}:
 38722.22783251229
   150.0073399014777

* Solving the normal equations:

$$A^T A x = A^T b$$

In [28]:
x = transpose(A)*A \ transpose(A)*b

2-element Vector{Float64}:
 38722.227832512304
   150.00733990147774

* Using the QR solution:

In [29]:
xhat3 = A\b

2-element Vector{Float64}:
 38722.227832512304
   150.00733990147825

* There are cases where we want to obtain and store the matrices Q and R from the factorization:

In [30]:
qrA = qr(A);                    # QR decomposition
xhat4 = qrA\b

2-element Vector{Float64}:
 38722.22783251231
   150.00733990147765

In [31]:
pred = xhat4[2]*A[:,2] + xhat4[1]*ones(N,1)

plot([scatter(x=dataBitcoin.Date, y=dataBitcoin.PriceFloat/1000, mode="markers+lines", name="Price"),
      scatter(x=dataBitcoin.Date, y=pred[:,1]/1000, mode="markers+lines", name="Prediction")],
     Layout(title="Bitcoin Price at 2022",  xaxis_title="Time (day - month)",  yaxis_title="Price (k\$)"))

data: [
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin, title, xaxis, and yaxis"

## Fitting an ellipse as Meyer (non-linear models)

Let's focus in an interesting curve-fitting problem, where we are given $n$ pairs of points 
$x_i,y_i$ and we want to find the ellipse which provides the best fit.

An idea can be start with the general conic that should satisfy this model:

$$a x^2 + bxy + c y^2 + dx + ey + f = 0$$

(Note that this is a second order equation, that will be quite important later in the course)

This model can be alternatively formulated as:

$$a x^2 + bxy + c y^2 + dx + ey = 1$$

Points in a particular ellipse should "satisfy" this equation (model). A particular ellipse (model) is parametrized by specific values of $a,b,c,d,e$. 

Therefore, given a set of observations $\{(x_i,y_i)_1^n\}$ the problem is find $a,b,c,d,e$ such that the following set of equations are satisfied:

$$a x_i^2 + b x_i y_i + c y_i^2 + dx_i + ey_i = 1, \qquad 1 \le i \le n$$

This problem can be formulated as a least squares problem by specifying a proper design matrix $A$, and solve the problem by using the previous formulation.

Let's generate noisy points around the ellipse.

In [32]:
θ = π/5; a = 2; b = 1.5; x_0 = 0; y_0 = 0;
fx(t) = a*cos(θ)*cos(t) - b*sin(θ)*sin(t) + x_0
fy(t) = a*sin(θ)*sin(t) + b*cos(θ)*cos(t) + y_0

N = 200;
ts = LinRange(0,2π,N);
x = fx.(ts) + randn(N)*0.1;
y = fy.(ts) + randn(N)*0.1;

plot([scatter(x=fx.(ts), y=fy.(ts), mode="line", name="Original Data"), 
      scatter(x=x, y=y, mode="markers", name="Noisy Data")],
     Layout(title="Non Linear Models - Data Creation",  xaxis_title="x",  yaxis_title="y"))

data: [
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin, title, xaxis, and yaxis"

Now we can construct the design matrix.

In [33]:
A = [x.^2 y.^2 x.*y x y ]

200×5 Matrix{Float64}:
 3.02346   1.85567   2.36866  1.73881   1.36223
 2.57897   1.71949   2.10583  1.60592   1.31129
 2.44903   1.39328   1.84721  1.56494   1.18037
 3.25687   1.42897   2.15731  1.80468   1.1954
 1.8535    2.32983   2.07806  1.36143   1.52638
 2.31962   2.05498   2.18329  1.52303   1.43352
 2.12434   2.34796   2.23335  1.45751   1.5323
 1.8702    2.11884   1.99064  1.36755   1.45562
 1.79567   2.0534    1.92021  1.34003   1.43297
 1.95177   2.39462   2.16189  1.39706   1.54746
 2.05279   2.71797   2.36208  1.43276   1.64863
 1.72141   2.63891   2.13134  1.31202   1.62447
 0.736648  2.546     1.36949  0.858282  1.59562
 ⋮                                      
 3.24109   0.549155  1.33411  1.8003    0.74105
 4.05737   0.730847  1.72201  2.01429   0.854896
 3.87447   0.805231  1.76631  1.96837   0.897347
 3.63606   0.673296  1.56465  1.90684   0.820546
 3.46843   0.843205  1.71015  1.86237   0.918262
 3.00828   0.743257  1.4953   1.73444   0.862123
 3.16653   0.956142  

We solve the least square problem by using the QR decomposition.

In [34]:
p = A\ones(N)

5-element Vector{Float64}:
  0.31435809249424157
  0.3759054125952335
 -0.20310932283735458
 -0.0015947475286378526
 -0.0006859668945522467

In [35]:
using Convex, SCS

b_t = ones(N)

# Create a (column vector) variable of size n x 1.
x_t = Variable(size(A,2))

# The problem is to minimize ||Ax - b||^2
# This can be done by: minimize(objective, constraints)
problem = minimize(square(norm(A * x_t - b_t)))

# Solve the problem by calling solve!
solve!(problem, SCS.Optimizer; silent_solver = true)

# Check the status of the problem
problem.status # :Optimal, :Infeasible, :Unbounded etc.

# Get the optimum value
p = x_t.value

5×1 Matrix{Float64}:
  0.31435809249370855
  0.3759054125944476
 -0.2031093228360795
 -0.0015947475286279757
 -0.0006859668945585962

We plot the solution:

In [36]:
X = LinRange(minimum(x),maximum(x),100)
Y = LinRange(minimum(y),maximum(y),100)
F = Array{Float64}(undef,100,100)

for i in 1:100, j in 1:100
    F[i,j] = p[1]*X[i]^2 + p[2]*Y[j]^2 + p[3]*X[i]*Y[j] + p[4]*X[i] + p[5]*Y[j]
end

plot([scatter(x=fx.(ts), y=fy.(ts), mode="line", name="Original Data", marker_color=:black),
      scatter(x=x, y=y, mode="markers", marker=attr(size=10, line_width=2, color=:yellow), name="Noisy Data"),
      contour(x=X, y=Y, z=F, linewidth=13, color=:green, name="Fitted Ellipse",  fill = false,  
        contours_coloring="lines",
        contours=attr(
            coloring ="heatmap",
            showlabels = true, # show labels on contours
            labelfont = attr(size = 12,color = "black",) # label font properties
        ),
        colorbar=attr(
            title="Level Contour", # title here
            titleside="right",
            titlefont=attr(size=14, family="Arial, sans-serif") )
     )], 
     Layout(title="Non Linear Models",  xaxis_title="x",  yaxis_title="y", legend=attr(x=-0.10, y=1.2,)))

data: [
  "scatter with fields marker, mode, name, type, x, and y",
  "scatter with fields marker, mode, name, type, x, and y",
  "contour with fields color, colorbar, contours, fill, linewidth, name, type, x, y, and z"
]

layout: "layout with fields legend, margin, title, xaxis, and yaxis"

# Homework 1

* Related with the nature of the data, which conditions should meet matrices $A$ and $b$ to be solvable from the least squares perspective.

* Use a least squares for non-linear models adjust the bitcoin price and perform a prediction using the model to determine the future daily price a week ahead, compare with the actual values.

* Use least squares to determine the relationship between the bitcoin price and prices of three comodities namely, oil, silved and gold, during the last year.

* Solve the [point set registration problem](https://en.wikipedia.org/wiki/Point-set_registration). Hint (check: S. Umeyama, Least-Squares Estimation of Transformation Parameters Between Two Point Patterns, IEEE Trans. Pattern Anal. Mach. Intell., vol. 13, no. 4, 1991). Construct a GUI to test.

# Solution

In [111]:
dataBitcoin = CSV.read("Datasets/BTC-USD.csv",DataFrame)
dataSilver = CSV.read("Datasets/silver_price.csv",DataFrame);
dataOil    = CSV.read("Datasets/BrentOilPrices.csv",DataFrame);
dataOil.Date = Dates.Date.(dataOil.Date, "m/d/Y")

dataGold   = CSV.read("Datasets/gold_price.csv",DataFrame);

xlim = Dates.DateTime.(["01/01/2020", "03/28/2022"], "m/d/Y")
p1 = plot(scatter(x=dataGold.date,    y= dataGold.price,         mode="markers+lines", name="Gold"), 
           Layout( xaxis_range=xlim, title="Bitcoin Price at 2022",  xaxis_title="Time (day - month)",  yaxis_title="Price (k\$)"));
p2 = plot(scatter(x=dataSilver.date,  y= dataSilver.price,       mode="markers+lines", name="Silver"), Layout( xaxis_range=xlim));
p3 = plot(scatter(x=dataOil.Date,     y= dataOil.Price,          mode="markers+lines", name="Oil"), Layout( xaxis_range=xlim));
p4 = plot(scatter(x=dataBitcoin.Date, y= dataBitcoin.Close/1000, mode="markers+lines", name="Bitcoin"), Layout( xaxis_range=xlim));


p = [p1 p2; p3 p4]
relayout!(p, title_text="Side by side layout (1 x 2)", xlim=xlim)
p

data: [
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis"
]

layout: "layout with fields annotations, margin, title, xaxis1, xaxis2, xaxis3, xaxis4, xlim, yaxis1, yaxis2, yaxis3, and yaxis4"